In [5]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

# Running the exploration on the full DVF 2024 filtered only on Paris

In [43]:
import pandas as pd

# Read the original file
df = pd.read_csv("full24.csv")

# Take first 2000 rows
df_paris = df[(df['code_postal'] >= 75000) & (df['code_postal'] < 76000)]
df_paris.to_csv("24_paris_eda.csv", index=False)

print(f"Created 24_paris_eda.csv with {len(df_paris)} rows")
print(f"Original file had {len(df)} rows")

<ipython-input-43-fe83bb48a2f2>:4: DtypeWarning:

Columns (8,10,12,14,16,17,18,20,22,24,35,36) have mixed types. Specify dtype option on import or set low_memory=False.



Created 24_paris_eda.csv with 74191 rows
Original file had 3458643 rows


In [44]:
# Basic stats
print("Number of rows : {}".format(df_paris.shape[0]))
print("Number of columns : {}".format(df_paris.shape[1]))
print()
print("Percentage of missing values: ")
display(100 * df_paris.isnull().sum() / df_paris.shape[0])
print()

Number of rows : 74191
Number of columns : 40

Percentage of missing values: 


id_mutation                       0.000000
date_mutation                     0.000000
numero_disposition                0.000000
nature_mutation                   0.000000
valeur_fonciere                   0.138831
adresse_numero                    0.004044
adresse_suffixe                  95.818900
adresse_nom_voie                  0.000000
adresse_code_voie                 0.000000
code_postal                       0.000000
code_commune                      0.000000
nom_commune                       0.000000
code_departement                  0.000000
ancien_code_commune             100.000000
ancien_nom_commune              100.000000
id_parcelle                       0.000000
ancien_id_parcelle              100.000000
numero_volume                    99.800515
lot1_numero                      11.792535
lot1_surface_carrez              62.527800
lot2_numero                      59.123074
lot2_surface_carrez              88.765484
lot3_numero                      93.323988
lot3_surfac

In [45]:
df_paris.dtypes

id_mutation                      object
date_mutation                    object
numero_disposition                int64
nature_mutation                  object
valeur_fonciere                 float64
adresse_numero                  float64
adresse_suffixe                  object
adresse_nom_voie                 object
adresse_code_voie                object
code_postal                     float64
code_commune                     object
nom_commune                      object
code_departement                 object
ancien_code_commune             float64
ancien_nom_commune               object
id_parcelle                      object
ancien_id_parcelle               object
numero_volume                    object
lot1_numero                      object
lot1_surface_carrez             float64
lot2_numero                      object
lot2_surface_carrez             float64
lot3_numero                      object
lot3_surface_carrez             float64
lot4_numero                      object


# Check nature_mutation

In [46]:
# Distribution of nature_mutation

# Value counts
print("Value counts for nature_mutation:")
print(df_paris['nature_mutation'].value_counts())
print()

# Percentage distribution
print("Percentage distribution:")
print(df_paris['nature_mutation'].value_counts(normalize=True) * 100)
print()

# Bar chart with plotly
fig = px.bar(
    x=df_paris['nature_mutation'].value_counts().index,
    y=df_paris['nature_mutation'].value_counts().values,
    title="Distribution of nature_mutation"
)
fig.update_layout(
    xaxis_title="Nature Mutation",
    yaxis_title="Count"
)
fig.show()

Value counts for nature_mutation:
nature_mutation
Vente                                 73123
Echange                                 659
Vente en l'état futur d'achèvement      246
Adjudication                            147
Vente terrain à bâtir                    16
Name: count, dtype: int64

Percentage distribution:
nature_mutation
Vente                                 98.560472
Echange                                0.888248
Vente en l'état futur d'achèvement     0.331577
Adjudication                           0.198137
Vente terrain à bâtir                  0.021566
Name: proportion, dtype: float64



## Conclusion = Keep only nature_mutation = "Vente"

In [47]:
df_paris = df_paris[df_paris['nature_mutation'] == 'Vente'].copy()

# Check type_local

In [50]:
# Value counts
print("Value counts for type_local:")
print(df_paris['type_local'].value_counts())
print()

# Percentage distribution
print("Percentage distribution:")
print(df_paris['type_local'].value_counts(normalize=True) * 100)
print()

# Bar chart with plotly
fig = px.bar(
    x=df_paris['type_local'].value_counts().index,
    y=df_paris['type_local'].value_counts().values,
    title="Distribution of type_local"
)
fig.update_layout(
    xaxis_title="Type Local",
    yaxis_title="Count"
)
fig.show()

Value counts for type_local:
type_local
Dépendance                                  35471
Appartement                                 32609
Local industriel. commercial ou assimilé     4663
Maison                                        136
Name: count, dtype: int64

Percentage distribution:
type_local
Dépendance                                  48.671085
Appartement                                 44.744028
Local industriel. commercial ou assimilé     6.398277
Maison                                       0.186611
Name: proportion, dtype: float64



## Conclusion = Keep only type_local =  "Appartement"

In [51]:
df_paris = df_paris[df_paris['type_local'] == 'Appartement'].copy()

In [52]:
df_paris.shape

(32609, 40)

# Check lots

In [53]:
# Analyse des NA pour les colonnes lots - Appartements uniquement

# Colonnes surface lots à analyser
lots_surface_columns = [
    'lot1_surface_carrez',
    'lot2_surface_carrez', 
    'lot3_surface_carrez',
    'lot4_surface_carrez',
    'lot5_surface_carrez'
]

print(f"Nombre total d'appartements: {len(df_paris)}")
print()

# Analyse des NA pour chaque colonne surface lots
print("Pourcentage de valeurs manquantes par colonne surface lots:")
for col in lots_surface_columns:
    if col in df_paris.columns:
        missing_pct = 100 * df_paris[col].isnull().sum() / len(df_paris)
        print(f"{col}: {missing_pct:.1f}%")

Nombre total d'appartements: 32609

Pourcentage de valeurs manquantes par colonne surface lots:
lot1_surface_carrez: 51.6%
lot2_surface_carrez: 87.2%
lot3_surface_carrez: 99.0%
lot4_surface_carrez: 99.8%
lot5_surface_carrez: 99.9%


In [54]:
print("Statistiques détaillées pour les surfaces des lots:")
for col in lots_surface_columns:
    if col in df_paris.columns:
        total = len(df_paris)
        missing = df_paris[col].isnull().sum()
        present = total - missing
        missing_pct = 100 * missing / total
        
        print(f"\n{col}:")
        print(f"  - Total: {total}")
        print(f"  - Valeurs présentes: {present}")
        print(f"  - Valeurs manquantes: {missing}")
        print(f"  - % manquant: {missing_pct:.1f}%")
        
        if present > 0:
            print(f"  - Surface min: {df_paris[col].min():.2f} m²")
            print(f"  - Surface max: {df_paris[col].max():.2f} m²")
            print(f"  - Surface moyenne: {df_paris[col].mean():.2f} m²")

Statistiques détaillées pour les surfaces des lots:

lot1_surface_carrez:
  - Total: 32609
  - Valeurs présentes: 15772
  - Valeurs manquantes: 16837
  - % manquant: 51.6%
  - Surface min: 1.00 m²
  - Surface max: 1587.00 m²
  - Surface moyenne: 50.06 m²

lot2_surface_carrez:
  - Total: 32609
  - Valeurs présentes: 4187
  - Valeurs manquantes: 28422
  - % manquant: 87.2%
  - Surface min: 0.93 m²
  - Surface max: 407.53 m²
  - Surface moyenne: 60.34 m²

lot3_surface_carrez:
  - Total: 32609
  - Valeurs présentes: 333
  - Valeurs manquantes: 32276
  - % manquant: 99.0%
  - Surface min: 0.65 m²
  - Surface max: 776.00 m²
  - Surface moyenne: 87.73 m²

lot4_surface_carrez:
  - Total: 32609
  - Valeurs présentes: 63
  - Valeurs manquantes: 32546
  - % manquant: 99.8%
  - Surface min: 9.01 m²
  - Surface max: 274.05 m²
  - Surface moyenne: 82.23 m²

lot5_surface_carrez:
  - Total: 32609
  - Valeurs présentes: 22
  - Valeurs manquantes: 32587
  - % manquant: 99.9%
  - Surface min: 1.00 m²
  -

# Note sur les lots DVF

## Problème identifié
- **lot1_surface_carrez** : 52% de valeurs manquantes
- **lot2_surface_carrez** : 87% de valeurs manquantes  
- **lot3-5** : 99%+ de valeurs manquantes

Les lots ne suivent **pas une logique séquentielle** :
- lot1 ≠ appartement principal
- lot2 peut être l'appartement, lot1 la cave
- Ordre dépend de la saisie notaire

## Recommandation pour le modèle
**À utiliser** :
- `nombre_lots` (fiable)
- Créer `nb_lots_surface` = nombre de lots avec surface
- Créer `a_plusieurs_lots` = booléen si plusieurs lots

In [55]:
# Création des features lots sur df_paris

# Nombre de lots avec surface renseignée
df_paris['nb_lots_surface'] = df_paris[['lot1_surface_carrez', 'lot2_surface_carrez', 
                                        'lot3_surface_carrez', 'lot4_surface_carrez', 
                                        'lot5_surface_carrez']].notna().sum(axis=1)

# Indicateur "a plusieurs lots"
df_paris['a_plusieurs_lots'] = (df_paris['nb_lots_surface'] > 1).astype(int)

# Vérification
print("Distribution nb_lots_surface:")
print(df_paris['nb_lots_surface'].value_counts().sort_index())
print()
print("Distribution a_plusieurs_lots:")
print(df_paris['a_plusieurs_lots'].value_counts())
print()
print("Pourcentage avec plusieurs lots:", 
      f"{df_paris['a_plusieurs_lots'].mean()*100:.1f}%")

Distribution nb_lots_surface:
nb_lots_surface
0    12609
1    19661
2      307
3       27
4        4
5        1
Name: count, dtype: int64

Distribution a_plusieurs_lots:
a_plusieurs_lots
0    32270
1      339
Name: count, dtype: int64

Pourcentage avec plusieurs lots: 1.0%


# Feature selection

In [59]:
print(df_paris.dtypes)

id_mutation                      object
date_mutation                    object
numero_disposition                int64
nature_mutation                  object
valeur_fonciere                 float64
adresse_numero                  float64
adresse_suffixe                  object
adresse_nom_voie                 object
adresse_code_voie                object
code_postal                     float64
code_commune                     object
nom_commune                      object
code_departement                 object
ancien_code_commune             float64
ancien_nom_commune               object
id_parcelle                      object
ancien_id_parcelle               object
numero_volume                    object
lot1_numero                      object
lot1_surface_carrez             float64
lot2_numero                      object
lot2_surface_carrez             float64
lot3_numero                      object
lot3_surface_carrez             float64
lot4_numero                      object


In [99]:
# Colonnes à GARDER pour le modèle
columns_to_keep = [
    # Target variable
    'valeur_fonciere',
    
    # Features temporelles (pour créer jour, mois, annee)
    'date_mutation',
    
    # Features géographiques (importantes selon tes modèles existants)
    'code_postal',              # Pour extraire arrondissement
    'longitude', 
    'latitude',
    
    # Features immobilières principales
    'surface_reelle_bati',      # Clé pour calculer prix_m2
    'nombre_pieces_principales',
    'type_local',               # Appartement, maison, etc.
    
    # Features lots (qu'on a créées)
    'nombre_lots',
    'nb_lots_surface',
    'a_plusieurs_lots'
]

In [100]:
df_model = df_paris[columns_to_keep].copy()

In [101]:
df_model.shape

(32609, 11)

# Prepare df_model (with the right columns selected) for EDA

In [102]:
df_model['prix_m2'] = df_model['valeur_fonciere'] / df_model['surface_reelle_bati']

In [103]:
# Conversion de date_mutation en datetime
df_model['date_mutation'] = pd.to_datetime(df_model['date_mutation'])

# Extraction des features temporelles
df_model['jour'] = df_model['date_mutation'].dt.day
df_model['mois'] = df_model['date_mutation'].dt.month
df_model['annee'] = df_model['date_mutation'].dt.year
df_model['arrondissement'] = df_model['code_postal'].astype(int) - 75000

# EDA on df_model

In [104]:
df_model.dtypes

valeur_fonciere                     float64
date_mutation                datetime64[ns]
code_postal                         float64
longitude                           float64
latitude                            float64
surface_reelle_bati                 float64
nombre_pieces_principales           float64
type_local                           object
nombre_lots                           int64
nb_lots_surface                       int64
a_plusieurs_lots                      int64
prix_m2                             float64
jour                                  int32
mois                                  int32
annee                                 int32
arrondissement                        int64
dtype: object

## Valeurs manquantes

In [105]:
# Valeurs manquantes
print("1. Valeurs manquantes par colonne:")
missing = df_model.isnull().sum()
missing_pct = 100 * missing / len(df_model)
missing_df = pd.DataFrame({
    'Missing': missing,
    'Percentage': missing_pct
}).sort_values('Missing', ascending=False)
print(missing_df[missing_df['Missing'] > 0])
print()

1. Valeurs manquantes par colonne:
                           Missing  Percentage
prix_m2                         48    0.147199
valeur_fonciere                 46    0.141065
longitude                       10    0.030666
latitude                        10    0.030666
surface_reelle_bati              2    0.006133
nombre_pieces_principales        2    0.006133



In [106]:
# Suppression des valeurs manquantes

print("Avant suppression des valeurs manquantes:")
print(f"Shape: {df_model.shape}")
print()

# Supprimer toutes les lignes avec des valeurs manquantes
df_model_clean = df_model.dropna().copy()

print("Après suppression des valeurs manquantes:")
print(f"Shape: {df_model_clean.shape}")
print(f"Lignes supprimées: {len(df_model) - len(df_model_clean)}")
print()

Avant suppression des valeurs manquantes:
Shape: (32609, 16)

Après suppression des valeurs manquantes:
Shape: (32551, 16)
Lignes supprimées: 58



## Analyse surface

In [107]:
# Visualisation des outliers surface_reelle_bati avec Plotly

# Box plot pour identifier visuellement les outliers
fig = px.box(
    df_model, 
    y='surface_reelle_bati',
    title="Distribution des surfaces - Identification des outliers"
)
fig.update_layout(
    yaxis_title="Surface réelle bâti (m²)"
)
fig.show()

In [108]:
# Histogramme pour voir la distribution
fig = px.histogram(
    df_model, 
    x='surface_reelle_bati',
    nbins=50,
    title="Distribution des surfaces réelles bâties"
)
fig.update_layout(
    xaxis_title="Surface réelle bâti (m²)",
    yaxis_title="Nombre de transactions"
)
fig.show()

In [109]:
surface_min = 10 
surface_max = 200

# Filtrer temporairement pour la visualisation
df_filtered_view = df_model[
    (df_model['surface_reelle_bati'] >= surface_min) & 
    (df_model['surface_reelle_bati'] <= surface_max)
]

# Histogramme sur les données filtrées
fig = px.histogram(
    df_filtered_view, 
    x='surface_reelle_bati',
    nbins=50,
    title=f"Distribution des surfaces entre {surface_min}m² et {surface_max}m²"
)

fig.update_layout(
    xaxis_title="Surface réelle bâti (m²)",
    yaxis_title="Nombre de transactions"
)

fig.show()

In [110]:
# Filtrage des surfaces entre 15 et 200 m²

# Nouveaux seuils
surface_min = 15   # m²
surface_max = 200  # m²

print("Avant filtrage surface:")
print(f"Shape: {df_model.shape}")
print(f"Surface min: {df_model['surface_reelle_bati'].min():.1f} m²")
print(f"Surface max: {df_model['surface_reelle_bati'].max():.1f} m²")
print(f"Surface moyenne: {df_model['surface_reelle_bati'].mean():.1f} m²")
print()

# Filtrage
df_model = df_model[
    (df_model['surface_reelle_bati'] >= surface_min) & 
    (df_model['surface_reelle_bati'] <= surface_max)
].copy()

print("Après filtrage surface:")
print(f"Shape: {df_model.shape}")
print(f"Surface min: {df_model['surface_reelle_bati'].min():.1f} m²")
print(f"Surface max: {df_model['surface_reelle_bati'].max():.1f} m²")
print(f"Surface moyenne: {df_model['surface_reelle_bati'].mean():.1f} m²")

Avant filtrage surface:
Shape: (32609, 16)
Surface min: 2.0 m²
Surface max: 1500.0 m²
Surface moyenne: 52.7 m²

Après filtrage surface:
Shape: (30239, 16)
Surface min: 15.0 m²
Surface max: 200.0 m²
Surface moyenne: 53.2 m²


## Analyse distribution prix_m2

In [111]:
df_model.head()

valeur_fonciere date_mutation  code_postal  longitude   latitude  \
3190767         562400.0    2024-01-05      75016.0   2.251902  48.838420   
3191534         580000.0    2024-01-15      75016.0   2.251124  48.843025   
3191713         880000.0    2024-01-19      75016.0   2.253974  48.835999   
3194736         252165.0    2024-03-20      75015.0   2.281940  48.830593   
3194756        1285000.0    2024-03-26      75016.0   2.251365  48.843634   

         surface_reelle_bati  nombre_pieces_principales   type_local  \
3190767                 55.0                        2.0  Appartement   
3191534                 78.0                        3.0  Appartement   
3191713                 85.0                        4.0  Appartement   
3194736                 34.0                        1.0  Appartement   
3194756                150.0                        4.0  Appartement   

         nombre_lots  nb_lots_surface  a_plusieurs_lots       prix_m2  jour  \
3190767            3                1                 0  10225.454545     5   
3191534            2                1                 0   7435.897436    15   
3191713            2                1                 0  10352.941176    19   
3194736            1                1                 0   7416.617647    20   
3194756            2                1                 0   8566.666667    26   

         mois  annee  arrondissement  
3190767     1   2024              16  
3191534     1   2024              16  
3191713     1   2024              16  
3194736     3   2024              15  
3194756     3   2024              16

In [112]:
# Statistiques descriptives
print("Statistiques prix_m2:")
print(df_model['prix_m2'].describe())
print()
print(f"Prix max: {df_model['prix_m2'].max():.0f} €/m²")
print(f"Prix > 20000€/m²: {(df_model['prix_m2'] > 20000).sum()} transactions")
print(f"Prix > 30000€/m²: {(df_model['prix_m2'] > 30000).sum()} transactions")
print(f"Prix < 2000€/m²: {(df_model['prix_m2'] < 2000).sum()} transactions")

Statistiques prix_m2:
count    3.020000e+04
mean     5.817846e+04
std      2.341257e+05
min      5.291005e-03
25%      8.233333e+03
50%      1.004045e+04
75%      1.315842e+04
max      1.593750e+07
Name: prix_m2, dtype: float64

Prix max: 15937500 €/m²
Prix > 20000€/m²: 4661 transactions
Prix > 30000€/m²: 3834 transactions
Prix < 2000€/m²: 1027 transactions


In [113]:
extreme_price = df_model[df_model['prix_m2'] == 15937500]

print("Ligne avec prix 15937500 €/m²:")
print(extreme_price)
print()

Ligne avec prix 15937500 €/m²:
         valeur_fonciere date_mutation  code_postal  longitude   latitude  \
3399912      255000000.0    2024-06-27      75008.0   2.307565  48.867236   

         surface_reelle_bati  nombre_pieces_principales   type_local  \
3399912                 16.0                        2.0  Appartement   

         nombre_lots  nb_lots_surface  a_plusieurs_lots     prix_m2  jour  \
3399912            0                0                 0  15937500.0    27   

         mois  annee  arrondissement  
3399912     6   2024               8  



In [114]:
# Box plot pour identifier visuellement les outliers
fig = px.box(
    df_model, 
    y='prix_m2',
    title="Distribution des prix au m² - Identification des outliers"
)
fig.update_layout(
    yaxis_title="Prix au m² (€)"
)
fig.show()

# Histogramme pour voir la distribution
fig = px.histogram(
    df_model, 
    x='prix_m2',
    nbins=50,
    title="Distribution des prix au m²"
)
fig.update_layout(
    xaxis_title="Prix au m² (€)",
    yaxis_title="Nombre de transactions"
)
fig.show()

In [115]:
# Histogramme avec limite à 50000€/m² pour voir la distribution normale
df_normal_prices = df_model[df_model['prix_m2'] <= 50000]

fig = px.histogram(
    df_normal_prices, 
    x='prix_m2',
    nbins=50,
    title="Distribution des prix au m² (limité à 50k€/m² pour clarté)"
)
fig.update_layout(
    xaxis_title="Prix au m² (€)",
    yaxis_title="Nombre de transactions"
)
fig.show()

In [116]:
fig = px.box(
    df_normal_prices, 
    y='prix_m2',
    title="Distribution des prix au m² - Box plot (limité à 50k€/m²)"
)
fig.update_layout(
    yaxis_title="Prix au m² (€)"
)
fig.show()

In [117]:
prix_min = 4000 
prix_max = 20000  

print("Avant filtrage prix_m2:")
print(f"Shape: {df_model.shape}")
print(f"Prix min: {df_model['prix_m2'].min():.0f} €/m²")
print(f"Prix max: {df_model['prix_m2'].max():.0f} €/m²")
print(f"Prix moyen: {df_model['prix_m2'].mean():.0f} €/m²")
print()

# Filtrage
df_model = df_model[
    (df_model['prix_m2'] >= prix_min) & 
    (df_model['prix_m2'] <= prix_max)
].copy()

print("Après filtrage prix_m2:")
print(f"Shape: {df_model.shape}")
print(f"Prix min: {df_model['prix_m2'].min():.0f} €/m²")
print(f"Prix max: {df_model['prix_m2'].max():.0f} €/m²")
print(f"Prix moyen: {df_model['prix_m2'].mean():.0f} €/m²")
print(f"Prix médian: {df_model['prix_m2'].median():.0f} €/m²")

Avant filtrage prix_m2:
Shape: (30239, 16)
Prix min: 0 €/m²
Prix max: 15937500 €/m²
Prix moyen: 58178 €/m²

Après filtrage prix_m2:
Shape: (24132, 16)
Prix min: 4000 €/m²
Prix max: 20000 €/m²
Prix moyen: 10036 €/m²
Prix médian: 9648 €/m²


## Analye nombre de pièces 

In [126]:
print(df_model['nombre_pieces_principales'].describe())


count    24132.000000
mean         2.378833
std          1.197616
min          0.000000
25%          2.000000
50%          2.000000
75%          3.000000
max         32.000000
Name: nombre_pieces_principales, dtype: float64


In [129]:
# 4. Box plot pour identifier les outliers
fig = px.box(
    df_model,
    y='nombre_pieces_principales',
    title="Distribution nombre de pièces - Identification outliers"
)
fig.update_layout(
    yaxis_title="Nombre de pièces principales"
)
fig.show()

In [130]:
print("Avant filtrage nombre de pièces:")
print(f"Shape: {df_model.shape}")
print(f"Pièces min: {df_model['nombre_pieces_principales'].min()}")
print(f"Pièces max: {df_model['nombre_pieces_principales'].max()}")
print()

# Filtrage
df_model = df_model[
    (df_model['nombre_pieces_principales'] >= 1) & 
    (df_model['nombre_pieces_principales'] <= 5)
].copy()

print("Après filtrage nombre de pièces:")
print(f"Shape: {df_model.shape}")
print(f"Pièces min: {df_model['nombre_pieces_principales'].min()}")
print(f"Pièces max: {df_model['nombre_pieces_principales'].max()}")
print()


Avant filtrage nombre de pièces:
Shape: (24132, 16)
Pièces min: 0.0
Pièces max: 32.0

Après filtrage nombre de pièces:
Shape: (23731, 16)
Pièces min: 1.0
Pièces max: 5.0



## Analyse géographique

In [131]:
df_model['arrondissement'].value_counts().sort_index()

arrondissement
1      218
2      309
3      524
4      396
5      703
6      532
7      638
8      490
9      862
10    1156
11    2019
12    1370
13    1313
14    1325
15    2666
16    1744
17    2026
18    2391
19    1377
20    1672
Name: count, dtype: int64

In [132]:
# 2. Prix moyen par arrondissement
prix_par_arrond = df_model.groupby('arrondissement')['prix_m2'].agg(['mean', 'median', 'count']).round(0)
prix_par_arrond.columns = ['Prix_moyen', 'Prix_median', 'Nb_transactions']
prix_par_arrond = prix_par_arrond.sort_values('Prix_moyen', ascending=False)

print("Prix par arrondissement (classé par prix moyen):")
print(prix_par_arrond)
print()

Prix par arrondissement (classé par prix moyen):
                Prix_moyen  Prix_median  Nb_transactions
arrondissement                                          
6                  13820.0      13861.0              532
7                  13465.0      13204.0              638
4                  12505.0      12567.0              396
1                  12464.0      12249.0              218
3                  11995.0      11770.0              524
8                  11964.0      11773.0              490
5                  11790.0      11704.0              703
2                  11421.0      11250.0              309
16                 10987.0      10729.0             1744
9                  10801.0      10621.0              862
17                 10298.0      10125.0             2026
11                  9945.0       9865.0             2019
15                  9732.0       9523.0             2666
14                  9570.0       9333.0             1325
10                  9545.0       9243.0

In [133]:
fig = px.bar(
    x=prix_par_arrond.index,
    y=prix_par_arrond['Prix_moyen'],
    title="Prix moyen au m² par arrondissement"
)
fig.update_layout(
    xaxis_title="Arrondissement",
    yaxis_title="Prix moyen (€/m²)"
)
fig.show()

In [134]:
# 4. Scatter plot géographique avec prix
fig = px.scatter(
    df_model,
    x='longitude',
    y='latitude',
    color='prix_m2',
    title="Répartition géographique des prix au m²",
    color_continuous_scale='Viridis'
)
fig.update_layout(
    xaxis_title="Longitude",
    yaxis_title="Latitude"
)
fig.show()

## Property impact analysis 

In [135]:
prix_par_pieces = df_model.groupby('nombre_pieces_principales')['prix_m2'].agg(['mean', 'median', 'count']).round(0)
prix_par_pieces.columns = ['Prix_moyen', 'Prix_median', 'Nb_transactions']

print("1. Prix par nombre de pièces:")
print(prix_par_pieces)
print()

fig = px.box(
    df_model,
    x='nombre_pieces_principales',
    y='prix_m2',
    title="Distribution des prix au m² par nombre de pièces"
)
fig.update_layout(
    xaxis_title="Nombre de pièces principales",
    yaxis_title="Prix au m² (€)"
)
fig.show()

1. Prix par nombre de pièces:
                           Prix_moyen  Prix_median  Nb_transactions
nombre_pieces_principales                                          
1.0                            9875.0       9516.0             5891
2.0                            9798.0       9430.0             8873
3.0                            9999.0       9653.0             5411
4.0                           10659.0      10306.0             2595
5.0                           11219.0      10935.0              961



In [137]:
# 1. Surface vs Prix au m² (relation inverse attendue)
fig = px.scatter(
    df_model,
    x='surface_reelle_bati',
    y='prix_m2',
    title="Relation Surface vs Prix au m²",
    opacity=0.6
)
fig.update_layout(
    xaxis_title="Surface réelle bâti (m²)",
    yaxis_title="Prix au m² (€)"
)
fig.show()

In [138]:
# 3. Impact des lots multiples
lots_impact = df_model.groupby('a_plusieurs_lots')['prix_m2'].agg(['mean', 'median', 'count']).round(0)
lots_impact.index = ['Sans lots multiples', 'Avec lots multiples']
lots_impact.columns = ['Prix_moyen', 'Prix_median', 'Nb_transactions']

print("2. Impact des lots multiples:")
print(lots_impact)
print()

fig = px.box(
    df_model,
    x='a_plusieurs_lots',
    y='prix_m2',
    title="Impact des lots multiples sur le prix au m²"
)
fig.update_layout(
    xaxis_title="Plusieurs lots (0=Non, 1=Oui)",
    yaxis_title="Prix au m² (€)"
)
fig.show()

2. Impact des lots multiples:
                     Prix_moyen  Prix_median  Nb_transactions
Sans lots multiples     10013.0       9621.0            23447
Avec lots multiples     10183.0       9852.0              284



## Correlation

In [142]:
numeric_features = [
    'prix_m2', 'surface_reelle_bati', 
    'nombre_pieces_principales', 'longitude', 'latitude', 
    'nombre_lots', 'nb_lots_surface', 'a_plusieurs_lots',
    'arrondissement', 'jour', 'mois', 'annee'
]

# Calcul de la matrice de corrélation
corr_matrix = df_model[numeric_features].corr()

In [ ]:
# Heatmap de corrélation complète
fig = px.imshow(
    corr_matrix,
    text_auto=True,
    aspect="auto",
    title="Matrice de corrélation - Toutes les features"
)
fig.update_layout(
    width=800,
    height=600
)
fig.show()

In [146]:
#  Visualisation des corrélations avec prix_m2
correlations_prix = corr_matrix['prix_m2'].sort_values(ascending=False)

fig = px.bar(
    x=correlations_prix.drop('prix_m2').values,
    y=correlations_prix.drop('prix_m2').index,
    orientation='h',
    title="Corrélations avec prix_m2 (target variable)"
)
fig.update_layout(
    xaxis_title="Corrélation",
    yaxis_title="Features"
)
fig.show()


# FAIRE UNIQUEMENT AVEC LES DONNEES NUMERIQUES

# Features finales - Smart Invest

## Target variable
- `prix_m2` (float) : Prix au mètre carré calculé

## Features numériques (5)
- `longitude` (float) : Coordonnée longitude
- `latitude` (float) : Coordonnée latitude
- `surface_reelle_bati` (float) : Surface en m²
- `nombre_pieces_principales` (float) : Nombre de pièces (1-5)
- `nombre_lots` (int) : Nombre total de lots
- `nb_lots_surface` (int) : Nombre de lots avec surface renseignée

## Features catégorielles (3)
- `arrondissement` (int) : Arrondissement parisien (1-20)
- `a_plusieurs_lots` (int) : Indicateur binaire (0/1)
- `annee` (int) : Année (2024)

## Total : 8 features + 1 target